In [ ]:
pip install beautifulsoup4

In [ ]:
pip install matplotlib

In [ ]:
pip install textblob

In [ ]:
pip install openpyxl

In [1]:
import pandas as pd
import requests
import re
from bs4 import BeautifulSoup
from dateutil import parser
import matplotlib.pyplot as plt
from textblob import TextBlob
from collections import Counter
from openpyxl import Workbook

## Try out for British Airways

In [1]:
"""notes"""
list1 = ['apple','banana']
dic1 = {l1: [] for l1 in list1}
dic1

{'apple': [], 'banana': []}

In [57]:
base_url = "https://www.airlinequality.com/airline-reviews/american-airlines/"
pagesize = 10
pages = 2
airline = "American Airline"
region = "America"

In [93]:
base_url = "https://www.airlinequality.com/airline-reviews/westjet/"
pagesize = 10
pages = 2
airline = "Westjet Airline"
region = "NA"

# Info of each Airline

In [96]:
url = base_url
response = requests.get(url)
content = response.content
soup = BeautifulSoup(content, 'html.parser')
### html.parser: python标准库,lxml是第三方解析库，需要安装C语言库（也可以支持xml,html）

Categories = ['Food & Beverages', 
              'Inflight Entertainment',
              'Seat Comfort', 
              'Staff Service', 
              'Value for Money']
ratings = {category: [] for category in Categories}
info = pd.DataFrame(columns=['Airline','star_airline', 'Review Count', 'Rating'] + Categories)

for div in soup.find_all('section', class_='comp_review-header'):

    category_values = {}
    for category in Categories:
        category_values[category] = "N/A"
        
    for row in div.find_all('tr'):
        header = row.find('td', class_='review-rating-header').text
        value = len(row.find_all('span', class_='star fill')) if row.find_all('span', class_='star fill') else "N/A"
        if header in Categories:
            category_values[header] = value

airline = soup.find("h1", itemprop="name").text.strip()
    
img_tags = soup.find_all('img')    
star_airline_img = soup.find('img', class_='skytrax-rating')
star_airline = re.search(r'\d+', star_airline_img['alt']).group() if star_airline_img else "N/A"
    
review_count = soup.find('span', itemprop='reviewCount').text.strip()

rating = soup.find('span', itemprop='ratingValue').text.strip()

info_new_row = pd.DataFrame({
            'Airline': [airline],
            'star_airline':[star_airline],
            'Review Count':[review_count],
            'Rating':[rating],
            **category_values
        })
        
info = pd.concat([info, info_new_row], ignore_index=True)
  

In [97]:
info

Airline star_airline Review Count Rating Food & Beverages  \
0  WestJet Airlines            3         1022      3                2   

  Inflight Entertainment Seat Comfort Staff Service Value for Money  
0                      2            2             3               2

In [41]:
# Create empty lists for ratings
categories = ['Seat Comfort', 'Cabin Staff Service', 'Food & Beverages', 
              'Inflight Entertainment', 'Ground Service', 'Wifi & Connectivity', 'Value For Money']
ratings = {category: [] for category in categories}

# Create an empty DataFrame
db = pd.DataFrame(columns=['Airline', 'Region',  'Title', 'Rating', 'Date Flown', 'Aircraft','Type_of_Traveller',
                           'Seat_Type','Route','Recommended', 'Review','Verified'] + categories)


for i in range(1, pages + 1):
    url = f"{base_url}/page/{i}/?sortby=post_date%3ADesc&pagesize={pagesize}"
    response = requests.get(url)
    content = response.content
    soup = BeautifulSoup(content, 'html.parser')
    ### html.parser: python标准库,lxml是第三方解析库，需要安装C语言库（也可以支持xml,html）

   
    for div in soup.find_all("article", itemprop="review"):
        # Extracting existing data (as previously done)
        rating = div.find("span", itemprop="ratingValue")
        rating = rating.text if rating else "N/A"
        
        title = div.find("h2", class_="text_header").get_text().strip('"')
        #strip('""')单括号里带双括号，为了移除双括号

        date = div.find("time", itemprop="datePublished")
        date = parser.parse(date.text).strftime('%Y-%m-%d') if date else "N/A"
        
        verified = 'No' if div.find('em', text='Not Verified') else 'Yes'
        # review = div.find("div", class_="text_content").get_text().strip('✅')
        review = div.find("div", class_="text_content").get_text().split('|', 1)[-1].strip()
        
        aircraft = div.find("td", class_="review-rating-header aircraft")
        aircraft = aircraft.find_next("td", class_="review-value").text if aircraft else "N/A"

        traveller = div.find("td", class_="review-rating-header type_of_traveller")
        traveller = traveller.find_next("td", class_="review-value").text if traveller else "N/A"
        
        seat_type = div.find("td", class_="review-rating-header cabin_flown")
        seat_type = seat_type.find_next("td", class_="review-value").text if seat_type else "N/A"
        
        route = div.find("td", class_="review-rating-header route")
        route = route.find_next("td", class_="review-value").text if route else "N/A"
        
        date_flown = div.find("td", text="Date Flown")
        date_flown = parser.parse(date_flown.find_next("td", class_="review-value").text).strftime('%Y-%m') if date_flown else "N/A"
        
        recommended = div.find("td", class_="review-rating-header recommended")
        recommended = recommended.find_next("td", class_=lambda x: x and x.startswith("review-value rating-")).text if recommended else "N/A"
        
        category_values = {}
        for category in categories:
            category_values[category] = "N/A"
        
        for row in div.find_all('tr'):
            header = row.find('td', class_='review-rating-header').text
            value = len(row.find_all('span', class_='star fill')) if row.find_all('span', class_='star fill') else "N/A"
            if header in categories:
                category_values[header] = value
        
        # Append the data to the DataFrame including star_airline
        db_new_row = pd.DataFrame({
            'Airline': [airline],
            'Aircraft': [aircraft],
            'Type_of_Traveller': [traveller],
            'Seat_Type': [seat_type],
            'Route': [route],
            'Region': [region],
            'Rating': [rating],
            'Title': [title],
            'Date_of_Review': [date],
            'Verified':[verified],
            'Review': [review],
            'Date Flown': [date_flown],
            'Recommended': [recommended],
            **category_values
        })
        
        db = pd.concat([db, db_new_row], ignore_index=True)


/var/folders/sf/sy4n06211kj1rhxq56l4y6_40000gn/T/ipykernel_14247/413808589.py:30: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  verified = 'No' if div.find('em', text='Not Verified') else 'Yes'
/var/folders/sf/sy4n06211kj1rhxq56l4y6_40000gn/T/ipykernel_14247/413808589.py:46: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  date_flown = div.find("td", text="Date Flown")
/var/folders/sf/sy4n06211kj1rhxq56l4y6_40000gn/T/ipykernel_14247/413808589.py:30: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  verified = 'No' if div.find('em', text='Not Verified') else 'Yes'
/var/folders/sf/sy4n06211kj1rhxq56l4y6_40000gn/T/ipykernel_14247/413808589.py:46: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  date_flown = div.find("td", text="Date Flown")
/var/folders/sf/sy4n06211kj1rhxq56l4y6

In [42]:
db

Airline   Region                                     Title  \
0   American Airline  America     expected better service from American   
1   American Airline  America                   went above and beyond"    
2   American Airline  America              The worst people to fly with   
3   American Airline  America   American Airlines is a 3rd rate carrier   
4   American Airline  America         Buyer Beware of American Airlines   
5   American Airline  America     nothing 'first' about this experience   
6   American Airline  America                     Horrible experience"    
7   American Airline  America            one of the worst airline trips   
8   American Airline  America          We experienced wonderful service   
9   American Airline  America  kindergarten level of quality of service   
10  American Airline  America                  “The worst airline ever”   
11  American Airline  America  “a consistent, safe and on-time product”   
12  American Airline  America         better off taking another airline   
13  American Airline  America           Overall nothing negative to say   
14  American Airline  America              nightmare of a return flight   
15  American Airline  America              she took out her frustration   
16  American Airline  America       I will never use this airline again   
17  American Airline  America       broke my trust in American Airlines   
18  American Airline  America      standard quality at reasonable price   
19  American Airline  America      “Avoid this airline like the plague”   

   Rating Date Flown        Aircraft Type_of_Traveller      Seat_Type  \
0       1    2023-10             N/A    Family Leisure  Economy Class   
1       9    2023-11             N/A      Solo Leisure  Economy Class   
2       1    2023-11             N/A          Business  Economy Class   
3       1    2023-11             N/A      Solo Leisure  Economy Class   
4       3    2023-11             N/A    Family Leisure  Economy Class   
5       8    2023-11  Boeing 777-300      Solo Leisure    First Class   
6       1    2023-11             N/A    Family Leisure  Economy Class   
7       2    2023-11      Boeing 787    Couple Leisure  Economy Class   
8      10    2023-10             N/A          Business    First Class   
9       1    2023-11             N/A      Solo Leisure  Economy Class   
10      2    2023-11             N/A          Business  Economy Class   
11      8    2023-11            A321          Business  Economy Class   
12      1    2023-11             N/A    Family Leisure  Economy Class   
13      9    2023-11            A321          Business  Economy Class   
14      2    2023-11             N/A    Couple Leisure  Economy Class   
15      6    2023-11             N/A    Couple Leisure  Economy Class   
16      1    2023-11             N/A      Solo Leisure  Economy Class   
17      1    2023-11             N/A    Couple Leisure  Economy Class   
18      1    2023-07             N/A    Family Leisure  Economy Class   
19      1    2023-10             N/A    Family Leisure  Economy Class   

                                     Route Recommended  \
0                      Munich to Charlotte          no   
1           North Carolina to Philadelphia         yes   
2                       Chicago to Memphis          no   
3   Detroit to Greenville via Philadelphia          no   
4                       Chicago to Orlando          no   
5                    Sydney to Los Angeles          no   
6              Punta Cana to Philadelphia           no   
7                   Philadelphia to Madrid          no   
8        Santa Ana to Santa Fe via Phoenix         yes   
9        Myrtle Beach to Fargo via Chicago          no   
10                Washington DC to Houston          no   
11               Charlotte to Philadelphia         yes   
12                     Dallas to San Diego          no   
13               Philadelphia to Charlotte         yes   
14               Dallas Ft Worth 

In [9]:
csv_file_name = f'{airline}_reviews.csv'
db.to_csv(csv_file_name, index=False)

## Define a function to implement the scrapping

In [99]:
def scrape_airline_info(base_url, airline):
    url = base_url
    response = requests.get(url)
    content = response.content
    soup = BeautifulSoup(content, 'html.parser')
    ### html.parser: python标准库,lxml是第三方解析库，需要安装C语言库（也可以支持xml,html）

    Categories = ['Food & Beverages', 
                'Inflight Entertainment',
                'Seat Comfort', 
                'Staff Service', 
                'Value for Money']
    ratings = {category: [] for category in Categories}
    info = pd.DataFrame(columns=['Airline','star_airline', 'Review Count', 'Rating'] + Categories)

    for div in soup.find_all('section', class_='comp_review-header'):

        category_values = {}
        for category in Categories:
            category_values[category] = "N/A"
            
        for row in div.find_all('tr'):
            header = row.find('td', class_='review-rating-header').text
            value = len(row.find_all('span', class_='star fill')) if row.find_all('span', class_='star fill') else "N/A"
            if header in Categories:
                category_values[header] = value

    airline = soup.find("h1", itemprop="name").text.strip()
        
    img_tags = soup.find_all('img')    
    star_airline_img = soup.find('img', class_='skytrax-rating')
    star_airline = re.search(r'\d+', star_airline_img['alt']).group() if star_airline_img else "N/A"
        
    review_count = soup.find('span', itemprop='reviewCount').text.strip()

    rating = soup.find('span', itemprop='ratingValue').text.strip()

    info_new_row = pd.DataFrame({
                'Airline': [airline],
                'star_airline':[star_airline],
                'Review Count':[review_count],
                'Rating':[rating],
                **category_values
            })
            
    info = pd.concat([info, info_new_row], ignore_index=True)
    return info
    

In [98]:


def scrape_airline_reviews(base_url, pages, airline, region):
    # Create empty lists for ratings
    categories = ['Seat Comfort', 'Cabin Staff Service', 'Food & Beverages', 
              'Inflight Entertainment', 'Ground Service', 'Wifi & Connectivity', 'Value For Money']
    ratings = {category: [] for category in categories}

    # Create an empty DataFrame
    db = pd.DataFrame(columns=['Airline', 'Region',  'Title', 'Rating', 'Date Flown', 'Aircraft','Type_of_Traveller',
                               'Seat_Type','Route','Recommended', 'Review','Verified'] + categories)


    for i in range(1, pages + 1):
        url = f"{base_url}/page/{i}/?sortby=post_date%3ADesc&pagesize=100"
        response = requests.get(url)
        content = response.content
        soup = BeautifulSoup(content, 'html.parser')

        for div in soup.find_all("article", itemprop="review"):
            rating = div.find("span", itemprop="ratingValue")
            rating = rating.text if rating else "N/A"
            
            title = div.find("h2", class_="text_header").get_text().strip('"')
            
            date = div.find("time", itemprop="datePublished")
            date = parser.parse(date.text).strftime('%Y-%m-%d') if date else "N/A"        
            
            verified = 'No' if div.find('em', text='Not Verified') else 'Yes'
            # review = div.find("div", class_="text_content").get_text().strip('✅')
            review = div.find("div", class_="text_content").get_text().split('|', 1)[-1].strip()
            
            aircraft = div.find("td", class_="review-rating-header aircraft")
            aircraft = aircraft.find_next("td", class_="review-value").text if aircraft else "N/A"
            
            traveller = div.find("td", class_="review-rating-header type_of_traveller")
            traveller = traveller.find_next("td", class_="review-value").text if traveller else "N/A"
            
            seat_type = div.find("td", class_="review-rating-header cabin_flown")
            seat_type = seat_type.find_next("td", class_="review-value").text if seat_type else "N/A"
            
            route = div.find("td", class_="review-rating-header route")
            route = route.find_next("td", class_="review-value").text if route else "N/A"

            date_flown = div.find("td", text="Date Flown")
            date_flown = parser.parse(date_flown.find_next("td", class_="review-value").text).strftime('%Y-%m') if date_flown else "N/A"

            recommended = div.find("td", class_="review-rating-header recommended")
            recommended = recommended.find_next("td", class_=lambda x: x and x.startswith("review-value rating-")).text if recommended else "N/A"

            category_values = {}

            category_values = {}
            for category in categories:
                category_values[category] = "N/A"
        
            for row in div.find_all('tr'):
                header = row.find('td', class_='review-rating-header').text
                value = len(row.find_all('span', class_='star fill')) if row.find_all('span', class_='star fill') else "N/A"
                if header in categories:
                    category_values[header] = value

            # Append the data to the DataFrame
            db_new_row = pd.DataFrame({
                'Airline': [airline],
                'Aircraft': [aircraft],
                'Type_of_Traveller': [traveller],
                'Seat_Type': [seat_type],
                'Route': [route],
                'Region': [region],
                'Rating': [rating],
                'Title': [title],
                'Date_of_Review': [date],
                'Verified':[verified],
                'Review': [review],
                'Date Flown': [date_flown],
                'Recommended': [recommended],
                **category_values
            })

            db = pd.concat([db, db_new_row], ignore_index=True)  

    return db

### List all the airlines

American Airlines  
Frontier Airlines  
Allegiant Air  
Qantas Airways  
Vueling Airlines  
Jet Airways  
Swiss Intl Air Lines  
WestJet Airlines  
Thai Airways

In [100]:
airlines = [
    {
        "name": "American_Airlines",
        "url":"https://www.airlinequality.com/airline-reviews/american-airlines/",
        "pages":59,
        "region":"America"
    },
    {
        "name": "Frontier_Airlines",
        "url":"https://www.airlinequality.com/airline-reviews/frontier-airlines",
        "pages":36,
        "region":"America"
    },
    {
        "name": "Allegiant_Air",
        "url":"https://www.airlinequality.com/airline-reviews/allegiant-air",
        "pages":20,
        "region":"America"
    },
    {
        "name": "Qantas_Airways",
        "url":"https://www.airlinequality.com/airline-reviews/qantas-airways",
        "pages":19,
        "region":"APAC"
    },
    {
        "name": "Vueling_Airlines",
        "url":"https://www.airlinequality.com/airline-reviews/vueling-airlines/",
        "pages":13,
        "region":"Europe"
    },
    {
        "name": "Jet_Airways",
        "url":"https://www.airlinequality.com/airline-reviews/jet-airways/",
        "pages":11,
        "region":"APAC"
    },
    {
        "name": "Swiss_Intl_Air_Lines",
        "url":"https://www.airlinequality.com/airline-reviews/swiss-international-air-lines/",
        "pages":11,
        "region":"Europe"
    },
    {
        "name": "WestJet_Airlines",
        "url":"https://www.airlinequality.com/airline-reviews/westjet/",
        "pages":11,
        "region":"Canada"
        #中转站，以加拿大为圆心
    },
    {
        "name": "Thai_Airways",
        "url":"https://www.airlinequality.com/airline-reviews/thai-airways",
        "pages":11,
        "region":"APAC"
    }
]

### Run the function and concatenate them into a single DataFrame

In [102]:
all_info = pd.DataFrame()
# Loop through each airline
for airline_info in airlines:
    airline_name = airline_info["name"]
    base_url = airline_info["url"]
    pages = airline_info["pages"]

    # Call the function for scraping reviews
    info = scrape_airline_info(base_url, airline)

    # Concatenate the reviews to the combined DataFrame
    all_info = pd.concat([all_info, info], ignore_index=True)

# Save the combined DataFrame to a CSV file
all_info.to_csv('combined_airline_info.csv', index=False)

In [103]:
all_info

Airline star_airline Review Count Rating Food & Beverages  \
0     American Airlines            3         5813      2                2   
1     Frontier Airlines            3         3547      2                1   
2         Allegiant Air            3         1939      3                2   
3        Qantas Airways            4         1854      6                3   
4      Vueling Airlines            3         1218      3                2   
5           Jet Airways            3         1060      5                3   
6  Swiss Intl Air Lines            4         1019      6                3   
7      WestJet Airlines            3         1022      3                2   
8          Thai Airways            4         1007      6                3   

  Inflight Entertainment Seat Comfort Staff Service Value for Money  
0                      2            2             2               2  
1                      1            2             2               1  
2                      1            2             2               2  
3                      3            3             4               3  
4                      1            2             2               2  
5                      2            3             3               3  
6                      3            3             4               3  
7                      2            2             3               2  
8                      3            4             4               4

In [104]:
all_reviews = pd.DataFrame()
pagesize = 100
# Loop through each airline
for airline_info in airlines:
    airline_name = airline_info["name"]
    base_url = airline_info["url"]
    # pagesize = airline_info["pagesize"]
    pages = airline_info["pages"]
    region = airline_info["region"]

    # Call the function for scraping reviews
    reviews = scrape_airline_reviews(base_url, pagesize, pages, airline_name, region)

    # Concatenate the reviews to the combined DataFrame
    all_reviews = pd.concat([all_reviews, reviews], ignore_index=True)

# Save the combined DataFrame to a CSV file
all_reviews.to_csv('combined_airline_reviews.csv', index=False)

/var/folders/sf/sy4n06211kj1rhxq56l4y6_40000gn/T/ipykernel_14247/151033424.py:27: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  verified = 'No' if div.find('em', text='Not Verified') else 'Yes'
/var/folders/sf/sy4n06211kj1rhxq56l4y6_40000gn/T/ipykernel_14247/151033424.py:43: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  date_flown = div.find("td", text="Date Flown")
/var/folders/sf/sy4n06211kj1rhxq56l4y6_40000gn/T/ipykernel_14247/151033424.py:27: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  verified = 'No' if div.find('em', text='Not Verified') else 'Yes'
/var/folders/sf/sy4n06211kj1rhxq56l4y6_40000gn/T/ipykernel_14247/151033424.py:43: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  date_flown = div.find("td", text="Date Flown")
/var/folders/sf/sy4n06211kj1rhxq56l4y6

In [105]:
all_reviews

Airline   Region                                    Title  \
0      American_Airlines  America    expected better service from American   
1      American_Airlines  America                  went above and beyond"    
2      American_Airlines  America             The worst people to fly with   
3      American_Airlines  America  American Airlines is a 3rd rate carrier   
4      American_Airlines  America        Buyer Beware of American Airlines   
...                  ...      ...                                      ...   
18474       Thai_Airways     APAC             Thai Airways customer review   
18475       Thai_Airways     APAC             Thai Airways customer review   
18476       Thai_Airways     APAC             Thai Airways customer review   
18477       Thai_Airways     APAC             Thai Airways customer review   
18478       Thai_Airways     APAC             Thai Airways customer review   

      Rating Date Flown Aircraft Type_of_Traveller       Seat_Type  \
0          1    2023-10      N/A    Family Leisure   Economy Class   
1          9    2023-11      N/A      Solo Leisure   Economy Class   
2          1    2023-11      N/A          Business   Economy Class   
3          1    2023-11      N/A      Solo Leisure   Economy Class   
4          3    2023-11      N/A    Family Leisure   Economy Class   
...      ...        ...      ...               ...             ...   
18474      7        N/A      N/A               N/A  Business Class   
18475     10        N/A      N/A               N/A   Economy Class   
18476      7        N/A      N/A               N/A   Economy Class   
18477     10        N/A      N/A               N/A  Business Class   
18478      9        N/A      N/A               N/A  Business Class   

                                        Route Recommended  \
0                         Munich to Charlotte          no   
1              North Carolina to Philadelphia         yes   
2                          Chicago to Memphis          no   
3      Detroit to Greenville via Philadelphia          no   
4                          Chicago to Orlando          no   
...                                       ...         ...   
18474                                     N/A         yes   
18475                                     N/A         yes   
18476                                     N/A         yes   
18477                                     N/A         yes   
18478                                     N/A         yes   

                                                  Review Verified  \
0      I pre booked 4 people (Myself, My wife whom sp...      Yes   
1      I recently had an experience with American Air...       No   
2      The worst people to fly with, never be there i...      Yes   
3      American Airlines has become a cheap airline t...       No   
4      Buyer Beware of American Airlines. Terrible ex...       No   
...                                                  ...      ...   
18474  RGN-BKK-AKL return. Service as usual with TG v...      Yes   
18475  London to Bangkok return. I found the staff ve...      Yes   
18476  Chiang Mai to Bangkok. I booked them because o...      Yes   
18477  HKG-BKK. Flew on A380. The whole trip from che...      Yes   
18478  SIN-BKK-TPE: SIN-BKK B773 service with the bra...      Yes   

      Seat Comfort Cabin Staff Service Food & Beverages  \
0                1                   5                2   
1                4                   5              N/A   
2                1                   1              N/A   
3                1                   1                3   
4                3                   3              N/A   
...            ...                 ...              ...   
18474            4                   3                4   
18475            4                   5                5   
18476            3                   4                3   
18477            5                   5                5   
18478            3          